<a href="https://www.kaggle.com/code/anishdivekar/forage-internship?scriptVersionId=109592573" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/forage-customer-data-and-segments/QVI_transaction_data.csv
/kaggle/input/purchase-behavior-dataset/purchase behaviou dataset.csv


# Import Libraries/ Modules

In [2]:
import csv
import matplotlib.pyplot as plt
import pandas as pd
import sqlite3 as sql
pd.set_option('display.max_columns', 20)
pd.set_option('display.width', 2000)
import pandas as pd
import plotly.express as px
import plotly.io as pio

# Read the CSV files using Pandas

In [3]:
transaction = pd.read_csv(r"../input/forage-customer-data-and-segments/QVI_transaction_data.csv")
behaviour = pd.read_csv("../input/purchase-behavior-dataset/purchase behaviou dataset.csv")

In [4]:
x = pd.DataFrame(behaviour)
print(x)

       LYLTY_CARD_NBR               LIFESTAGE PREMIUM_CUSTOMER
0                1000   YOUNG SINGLES/COUPLES          Premium
1                1002   YOUNG SINGLES/COUPLES       Mainstream
2                1003          YOUNG FAMILIES           Budget
3                1004   OLDER SINGLES/COUPLES       Mainstream
4                1005  MIDAGE SINGLES/COUPLES       Mainstream
...               ...                     ...              ...
72632         2370651  MIDAGE SINGLES/COUPLES       Mainstream
72633         2370701          YOUNG FAMILIES       Mainstream
72634         2370751          YOUNG FAMILIES          Premium
72635         2370961          OLDER FAMILIES           Budget
72636         2373711   YOUNG SINGLES/COUPLES       Mainstream

[72637 rows x 3 columns]


# See Columns in trasaction and Behavior Table

In [5]:
for x in transaction:
    print (x)

DATE
STORE_NBR
LYLTY_CARD_NBR
TXN_ID
PROD_NBR
PROD_NAME
PROD_QTY
TOT_SALES


In [6]:
for y in behaviour:
    print(y)

LYLTY_CARD_NBR
LIFESTAGE
PREMIUM_CUSTOMER


# Explore the data of each table

In [7]:
print("Below shows the datatypes and null counts in tables")
print(transaction.info())
print(behaviour.info())

print("Below shows the count of unique values in tables")
print(transaction.nunique())
print(behaviour.nunique())

Below shows the datatypes and null counts in tables
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 264836 entries, 0 to 264835
Data columns (total 8 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   DATE            264836 non-null  int64  
 1   STORE_NBR       264836 non-null  int64  
 2   LYLTY_CARD_NBR  264836 non-null  int64  
 3   TXN_ID          264836 non-null  int64  
 4   PROD_NBR        264836 non-null  int64  
 5   PROD_NAME       264836 non-null  object 
 6   PROD_QTY        264836 non-null  int64  
 7   TOT_SALES       264836 non-null  float64
dtypes: float64(1), int64(6), object(1)
memory usage: 16.2+ MB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 72637 entries, 0 to 72636
Data columns (total 3 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   LYLTY_CARD_NBR    72637 non-null  int64 
 1   LIFESTAGE         72637 non-null  object
 2   PREMIUM_CUSTO

# Create a database and store the csv data in the database. 
# Here the database will be named "forage"

In [8]:
forage='forage.db'
connection=sql.connect(forage)

# Create cursor object to execute queries in the database.

In [9]:
cursor=connection.cursor()

# **Make table in the database and input the csv file data into the tables.**

In [10]:
cursor.execute("""CREATE TABLE tran
(DATE int,
STORE_NBR int,
LYLTY_CARD_NBR int,
TXN_ID int,
PROD_NBR int,
PROD_NAME text,
PROD_QTY int,
TOT_SALES int)""")

In [11]:
cursor.execute("""
CREATE TABLE behave
(LYLTY_CARD_NBR integer,
LIFESTAGE object,
PREMIUM_CUSTOMER object)""")

# Transfer data from csv files to the SQL database forage

In [12]:
transaction.to_sql("tran",connection,if_exists='append',index=False)
behaviour.to_sql("behave", connection, if_exists='append', index=False)

# **Join the two tables on common column which is LYLTY_CARD_NBR**

In [13]:
cursor.execute("""CREATE TABLE customer_behaviour AS
SELECT *
FROM tran
JOIN behave ON tran.LYLTY_CARD_NBR = behave.LYLTY_CARD_NBR""")

In [14]:
df=pd.read_sql_query("""SELECT * FROM customer_behaviour""", connection)
print(df.head())

    DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR                                 PROD_NAME  PROD_QTY  TOT_SALES  LYLTY_CARD_NBR:1               LIFESTAGE PREMIUM_CUSTOMER
0  43390          1            1000       1         5    Natural Chip        Compny SeaSalt175g         2        6.0              1000   YOUNG SINGLES/COUPLES          Premium
1  43599          1            1307     348        66                  CCs Nacho Cheese    175g         3        6.3              1307  MIDAGE SINGLES/COUPLES           Budget
2  43605          1            1343     383        61    Smiths Crinkle Cut  Chips Chicken 170g         2        2.9              1343  MIDAGE SINGLES/COUPLES           Budget
3  43329          2            2373     974        69    Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0              2373  MIDAGE SINGLES/COUPLES           Budget
4  43330          2            2426    1038       108  Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8    

# Import pandas profiling module for easy EDA

In [15]:
import pandas_profiling
%pip install ipywidgets

Note: you may need to restart the kernel to use updated packages.


In [16]:
data = pd.read_sql_query("""SELECT * FROM customer_behaviour""", connection)

In [17]:
data.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Highest sold product

In [18]:
top_sold = pd.read_sql_query("""
SELECT PROD_NBR,PROD_NAME,SUM(TOT_SALES) AS SALES
FROM customer_behaviour 
GROUP BY PROD_NBR
ORDER BY SALES DESC
LIMIT 10""",connection)

print(top_sold)

   PROD_NBR                                 PROD_NAME    SALES
0         4          Dorito Corn Chp     Supreme 380g  40352.0
1        14    Smiths Crnkle Chip  Orgnl Big Bag 380g  36367.6
2        16  Smiths Crinkle Chips Salt & Vinegar 330g  34804.2
3       102    Kettle Mozzarella   Basil & Pesto 175g  34457.4
4         7         Smiths Crinkle      Original 330g  34302.6
5        23                      Cheezels Cheese 330g  34296.9
6        20          Doritos Cheese      Supreme 330g  33390.6
7        89   Kettle Sweet Chilli And Sour Cream 175g  33031.8
8        46                      Kettle Original 175g  32740.2
9        32      Kettle Sea Salt     And Vinegar 175g  32589.0


#sales_by_qty = sales_by_qty.sort_values(by="SALES") --- To arrange the graph by adjusting the columns
vis=px.bar(top_sold, x=top_sold.PROD_NAME, y=top_sold.SALES, color = top_sold.SALES)
vis.show()

# HIGHEST SOLD PRODUCT BY QUANTITY

In [19]:
sales_by_qty=pd.read_sql_query("""
SELECT PROD_QTY,PROD_NBR, PROD_NAME, SUM(TOT_SALES) AS SALES
FROM customer_behaviour
GROUP BY PROD_QTY, PROD_NBR
ORDER BY SALES DESC
LIMIT 100""",connection)

print(sales_by_qty)

    PROD_QTY  PROD_NBR                                 PROD_NAME    SALES
0          2         4          Dorito Corn Chp     Supreme 380g  37232.0
1          2        14    Smiths Crnkle Chip  Orgnl Big Bag 380g  33901.4
2          2        16  Smiths Crinkle Chips Salt & Vinegar 330g  32809.2
3          2       102    Kettle Mozzarella   Basil & Pesto 175g  32443.2
4          2         7         Smiths Crinkle      Original 330g  32398.8
..       ...       ...                                       ...      ...
95         2       107  Smiths Crinkle Cut  French OnionDip 150g   6505.2
96         2        38   Infuzions Mango     Chutny Papadums 70g   6307.2
97         2        94                         Burger Rings 220g   6283.6
98         2        54                         CCs Original 175g   5623.8
99         2        91                  CCs Tasty Cheese    175g   5569.2

[100 rows x 4 columns]


In [20]:
qty_breakdown =px.line(sales_by_qty, x=sales_by_qty.PROD_NAME, y=sales_by_qty.SALES, color=sales_by_qty.PROD_QTY)
qty_breakdown.show()
print ("Highest sold products are sold in pair (QTY-2)")


Highest sold products are sold in pair (QTY-2)


# SALES BY CUSTOMER SEGMENT

In [21]:
customer_contribution = pd.read_sql_query("""
SELECT LIFESTAGE, PROD_NAME, SUM(TOT_SALES) AS SALES
FROM customer_behaviour
GROUP BY LIFESTAGE, PROD_NAME
ORDER BY SALES DESC
LIMIT 10""", connection)

print(customer_contribution)

               LIFESTAGE                                 PROD_NAME    SALES
0  OLDER SINGLES/COUPLES          Dorito Corn Chp     Supreme 380g  8459.75
1         OLDER FAMILIES          Dorito Corn Chp     Supreme 380g  7982.00
2  OLDER SINGLES/COUPLES    Smiths Crnkle Chip  Orgnl Big Bag 380g  7528.40
3               RETIREES          Dorito Corn Chp     Supreme 380g  7527.00
4  OLDER SINGLES/COUPLES  Smiths Crinkle Chips Salt & Vinegar 330g  7182.00
5  OLDER SINGLES/COUPLES         Smiths Crinkle      Original 330g  7130.70
6  OLDER SINGLES/COUPLES                      Cheezels Cheese 330g  7119.30
7  OLDER SINGLES/COUPLES      Kettle Sea Salt     And Vinegar 175g  7036.20
8               RETIREES    Smiths Crnkle Chip  Orgnl Big Bag 380g  7026.90
9  OLDER SINGLES/COUPLES          Kettle Honey Soy    Chicken 175g  7025.40


In [22]:
customer_segment = px.bar(customer_contribution, x=customer_contribution.LIFESTAGE,y= customer_contribution.SALES, color=customer_contribution.PROD_NAME)
customer_segment.show()
print("Older singles/ couples contribute highest towards top 10 selling products")

Older singles/ couples contribute highest towards top 10 selling products


In [23]:
sales_contribution_by_segment = pd.read_sql_query("""
SELECT LIFESTAGE, SUM(TOT_SALES) AS SALES
FROM customer_behaviour
GROUP BY LIFESTAGE
ORDER BY SALES DESC""", connection)

print(sales_contribution_by_segment)

                LIFESTAGE      SALES
0   OLDER SINGLES/COUPLES  402426.75
1                RETIREES  366470.90
2          OLDER FAMILIES  353767.20
3          YOUNG FAMILIES  316160.10
4   YOUNG SINGLES/COUPLES  260405.30
5  MIDAGE SINGLES/COUPLES  184751.30
6            NEW FAMILIES   50433.45


In [24]:
sales_per_segment = px.pie(sales_contribution_by_segment, values=sales_contribution_by_segment.SALES, names = sales_contribution_by_segment.LIFESTAGE)
sales_per_segment.show()

# Conclusion

The correlations in the explored data gave insights to relations between sales of different products and segments that are contributing to the sales. 

1. Highest Sold Product
List of top 10 products in terms of sales were visualized. Product number 4 was the top selling product that made the highest sale of approximately 40.3K. Product 32 was the top 10th sold product with the sale of 32.5K. 


2. Product sale by Quantity
A trend of products sold in a pair of 2 were seen to make highest contribution to sales. The top 100 sold products were found with highest sales were sold in a **pair of 2** according to the trend visualized. 

3. Sales by customer segment
The top sold product Dorito corn chip was bought mostly by OLDER SINGLES/ COUPLES. In addition, OLDER SINGLES/ COUPLES have contributed significanty to oveall sales of different products in the markets. 

4. Customer contributions to sales. 
It is observed that older singles/ couples segment of customers have contributed almost 21% to total sales according to the data followed by retirees customer data. 
